In [3]:
import pandas as pd
import numpy as np
from surprise import Dataset
from surprise import Reader
from surprise.prediction_algorithms.matrix_factorization import SVD as FunkSVD
from surprise.model_selection import train_test_split
import matplotlib.pyplot as plt
import ast
from gensim.models import Word2Vec
import string
from nltk import WordNetLemmatizer
import re
import unidecode
from sklearn.metrics.pairwise import cosine_similarity
import warnings


pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
warnings.filterwarnings('ignore')

# Hybrid Recommendation Approach
Based on our findings from our collaborative and content-based recommender, we determined that our best plan going to use a hybrid model and combine both models. As discovered when preparing our content-based and collaborative model, our intital goal of recommending multiple recipes with the same ingredients to produce a groceyr list is not going to work. What we are going to do going forward will be to simply our plan. We will recommend one new recipe to our selected user based on their input of ingredients. <br>

The way we will do this is to generate a list of recipes first through the collaborative filtering system, which will refine the list of recipes with new recipes that user may like. With the refined list of recipes, we will then use the content-based recommender system to filter top N recipes that are most similar to what the user has inputted.

In [4]:
#Import recipes data
df = pd.read_csv('Cleaned_recipes.csv')

In [5]:
#Import review data
df_review = pd.read_csv('Cleaned_reviews.csv')

In [6]:
df.drop(columns = 'Unnamed: 0', inplace = True)

In [7]:
df_review.drop(columns = 'Unnamed: 0', inplace = True)

## Collaborative model FunkSVD - refining the initial list of recipes

In [8]:
#Initializing FunkSVD algorithm
my_reader = Reader(rating_scale = (1,5))

df_review_data = Dataset.load_from_df(df_review, my_reader)

#Build full trainset
full_trainset = df_review_data.build_full_trainset()

#Build Funk SVD algorithm with optimized parameters
review_algo = FunkSVD(n_factors = 10,
                     n_epochs = 100,
                     lr_all = 0.005,
                     biased = False,
                     verbose = 0)

#Fit with full trainset
review_algo.fit(full_trainset)

In [9]:
#Getting Latent Variables
User = review_algo.pu
Item = review_algo.qi.T

In [12]:
#FunkSVD recommendation
def get_recommendations_1(input_user, N):
    """
    Function will provide top N recipes based on ratings for the input_user.
    
    input_user: User id
    N: parameters for top number of recipes to return
    
    Output: Dataframe with top N recipes sort by ratings
    
    """
    inner_user_id = full_trainset.to_inner_uid(input_user)
    user_profile = User[inner_user_id]

    rated_recipes = df_review[df_review['User'] == input_user]['RecipeId']

    unrated_recipes = df_review[~df_review['RecipeId'].isin(rated_recipes)]['RecipeId'].unique()

    rating_list = []
    for val in unrated_recipes:
        input_recipe = val

        inner_recipe_id = full_trainset.to_inner_iid(input_recipe)
        recipe_profile = Item[:, inner_recipe_id]

        rating = np.dot(user_profile, recipe_profile)
        rating_list.append(rating)

    min_rating = np.min(rating_list)
    max_rating = np.max(rating_list)

    mapped_rating_list = []
    for rating in rating_list:
        # Map the rating to a 1-5 scale
        mapped_rating = 1 + (rating - min_rating) / (max_rating - min_rating) * 4
        mapped_rating_list.append(mapped_rating)

    top_indices = np.argsort(mapped_rating_list)[::-1][:N]
    top_recipes = [unrated_recipes[i] for i in top_indices]
    top_ratings = [mapped_rating_list[i] for i in top_indices]
    top_recipes_names = [df.loc[df['RecipeId'] == i, 'RecipeName'].iloc[0] for i in top_recipes]
    ingredients = [df.loc[df['RecipeId'] == i, 'ingredients'].iloc[0] for i in top_recipes]
    
    recommendations_df = pd.DataFrame({'RecipeName': top_recipes_names, 'Rating': top_ratings, 'ingredients': ingredients})
    return recommendations_df

In [13]:
df_refined = get_recommendations_1(2312,100)

In [14]:
df_refined

RecipeName    Rating  \
0         Extremely Soft White Bread  (Bread Machine)  5.000000   
1                         Bahama Mama Banana Rum Cake  4.867263   
2   A1b Bacon Burger Bites on White Polenta Cakes #A1  4.853836   
3   Copy-Cat Panera Cream of Chicken and Wild Rice...  4.823795   
4                                Texas Chewy Pralines  4.761721   
5                                      Elderberry Pie  4.749467   
6                           Easy Cream of Potato Soup  4.730810   
7     Old Fashioned Molasses &quot;caramel&quot; Corn  4.730153   
8                              Donair Meat Sandwiches  4.716243   
9                                    Oven Baked Tacos  4.703420   
10                        Easy No-Knead Challah Bread  4.675762   
11                                 Homemade Bratwurst  4.674966   
12                           Grape Salad With a Twist  4.672850   
13                Chili's Fire-Grilled Corn Guacamole  4.672711   
14  &quot;perfect Chocolate Cake&quot; Mccall's Co...  4.672152   
15                       The Best Teriyaki Beef Jerky  4.671362   
16          Irish Soda Bread with Raisins and Caraway  4.666440   
17           Biscuits &amp; Gravy Breakfast Casserole  4.658338   
18                            Deep Fried French Toast  4.652448   
19               Luby's Cafeteria's Spanish Cole Slaw  4.648164   
20       Basic Vinaigrette Dressing With 8 Variations  4.647724   
21  Cinnamon-Pumpkin Empanadas ( Empanadas De Cala...  4.639650   
22           Sweet &amp; Spicy Roasted Kabocha Squash  4.638399   
23  Sugar-Free French Vanilla Ice Cream (With Xyli...  4.633307   
24                              Drop Scones (So Easy)  4.632983   
25                            Sweet Corn Tamale Cakes  4.629877   
26                        Fresh Egg Pasta-Gluten Free  4.627580   
27                        Fig &amp; Goat Cheese Nests  4.623721   
28                   Fall-Off-The-Bone Baby Back Ribs  4.623596   
29                     Shrimp &amp; Coconut Soup #RSC  4.622304   
30                                     Sindhi Biryani  4.622035   
31  Pastry Dough (Madam Benoit's No Fail Lemon Tan...  4.620922   
32                           Slammin Blackened Salmon  4.619581   
33       Egg Free, No-Bake Cookie Dough (For Eating!)  4.618866   
34                               Best Ever Bruschetta  4.618367   
35                                    Easy Quick Buns  4.618104   
36                              Grilled Shrimp Kabobs  4.617486   
37                Quick and Easy Eggless Banana Bread  4.616237   
38                          Delicious Fluffy Pancakes  4.615931   
39                         Moist Chocolate Pound Cake  4.614778   
40                             Best Pecan Pie (Tarts)  4.612745   
41                                  Vegan Banana Cake  4.611942   
42                     White Asparagus in White Sauce  4.611180   
43                          Black Bean Chocolate Cake  4.610672   
44                             Grilled Bourbon Salmon  4.608550   
45            Blueberry Pancakes, Milk-free, Egg-free  4.607195   
46    The Best Sour Cream Shredded Chicken Enchiladas  4.601800   
47                                     Michigan Sauce  4.600986   
48                                        Sesame Tofu  4.600425   
49  Pumpkin Cheesecake (A Cheesecake Factory Copycat)  4.597671   
50   6 Layer Dreamy Chocolate Mousse Cake- Paula Deen  4.594238   
51  The World's Best Bread Machine Pizza Dough Recipe  4.594047   
52              Sausage-Stuffed Banana Pepper Hotdish  4.591246   
53                    Pressure Cooker Corn on the Cob  4.589684   
54                          Salsa Chicken Sooooo Easy  4.588068   
55                        Barefoot Contessa's Lasagna  4.587874   
56                                     Microwave Roux  4.586513   
57                           Oven Crisp Chicken Wings  4.586240   
58  Pistachio-Crusted Pork Scaloppine with Mango S...  4.584262   
59                     

In [15]:
type(df_refined['ingredients'][0])

str

# Content-Based Recommender

In [16]:
#Change String to List
df_refined['ingredients'] = df_refined['ingredients'].apply(lambda s: list(ast.literal_eval(s)))

In [17]:
#Ingredient preprocess function
def ingredient_preprocess(ingredients):
        
    ingrd_list = []
    translator = str.maketrans('','', string.punctuation)
    num_pattern = r'[0-9]'
    non_alphabet = r'[\W_]'
    lemmatizer = WordNetLemmatizer()
    for i in ingredients:
        #remove punctuations
        items = i.translate(translator)
        
        #Making all characters lowercase
        items = i.lower()
        
        #remove any numbers
        items = re.sub(num_pattern, ' ', items)
        
        #remove accents
        items = unidecode.unidecode(items)
        
        #remove any non-alphabet characters
        items = re.sub(non_alphabet, ' ', items)
        
        #Lemmatize words
        items = lemmatizer.lemmatize(items)
        
        ingrd_list.append(items)
    return ingrd_list
   

In [18]:
#Clean up output of ingredients from recommendation
def ingredient_parser_final(ingredient):
    """
    cleanup ingredients output
    """
    if isinstance(ingredient, list):
        ingredients = ingredient
    else:
        ingredients = ast.literal_eval(ingredient)

    ingredients = ",".join(ingredients)
    ingredients = unidecode.unidecode(ingredients)
    return ingredients

In [19]:
#To sort ingredients list in alphabetical order
def get_and_sort_corpus(data):
    corpus_sorted = []
    for doc in data['ingredients'].values:
        doc.sort()
        corpus_sorted.append(doc)
    return corpus_sorted

In [20]:
type(df_refined['ingredients'][0])

list

In [21]:
ingredients_corpus = get_and_sort_corpus(df_refined)

In [22]:
#Building Word2Vec model with vec size of 150
total_lengths = [len(ingredients) for ingredients in df_refined['ingredients']]
avg_len = sum(total_lengths) / len(total_lengths)

model_Word2Vec = Word2Vec(ingredients_corpus, 
                          sg = 0, 
                          workers = 3, 
                          min_count = 1, 
                          window = avg_len, 
                          vector_size = 150)

w2v = {word: model_Word2Vec.wv[word] for word in model_Word2Vec.wv.key_to_index}

In [23]:
class MeanEmbeddingVectorizer(object):
    
    def __init__(self, model_Word2Vec):
        self.model_Word2Vec = model_Word2Vec
        self.vector_size = model_Word2Vec.wv.vector_size
    
    def transform(self, docs):
        doc_word_vector = self.doc_average_list(docs)
        return doc_word_vector
    
    def doc_average(self, doc):
        """
        Compute average word vector for a recipe's ingredient
        
        :param doc: list of ingredients
        :return
            mean: float of average word vectors
        
        """
        
        
        mean = []
        for word in doc:
            if word in self.model_Word2Vec.wv.index_to_key:
                mean.append(self.model_Word2Vec.wv.get_vector(word))
                
        if not mean: #empty words
            #If text empty, return vector of zeros
            return np.zeros(self.vector_size)
        else:
            mean = np.array(mean).mean(axis = 0)
            return mean
        
    def doc_average_list(self, docs):
        """
        Compute average word vector for multiple docs (doc has been tokenized)
        
        :param docs: list of recipes in list of tokens
        :return
            array of average word vector
        
        """
        return np.vstack([self.doc_average(doc) for doc in docs])

In [24]:
#Cosine Recommendation
def get_recommendations(N, scores):
    """
    Rank scores and output a pandas data frame containing all the details of the top N recipes.
    :param scores: list of cosine similarities
    """
    # order the scores with and filter to get the highest N scores
    top = sorted(range(len(scores)), key=lambda i: scores[i], reverse=True)[:N]
    # create dataframe to load in recommendations
    recommendation = pd.DataFrame(columns=["recipe", "ingredients", "score","rating"])
    count = 0
    for i in top:
        recommendation.loc[count, "recipe"] = df_refined["RecipeName"][i]
        recommendation.loc[count, "ingredients"] = df_refined["ingredients"][i]
        recommendation.loc[count, "score"] = f"{scores[i]}"
        recommendation.loc[count, "rating"] = df_refined['Rating'][i]
        count += 1
    return recommendation

def get_recs_cosine(ingredients, N=5):
    """
    Get the top N recipe recomendations.
    :param ingredients: comma seperated string listing ingredients
    :param N: number of recommendations
    """
    # load in word2vec model
    model = model_Word2Vec
    # normalize embeddings
    model.init_sims(replace=True)
    # load in data
    data = df_refined
    # create corpus
    corpus = get_and_sort_corpus(data)

    # get average embdeddings for each document
    mean_vec_tr = MeanEmbeddingVectorizer(model_Word2Vec)
    doc_vec = mean_vec_tr.transform(corpus)
    doc_vec = [doc.reshape(1, -1) for doc in doc_vec]
    assert len(doc_vec) == len(corpus)
    

    # create embeddings for input text
    input = ingredients
    # create tokens with elements
    input = input.split(",")
    # parse ingredient list
    input = ingredient_preprocess(input)
    # get embeddings for ingredient doc
    input_embedding = mean_vec_tr.transform([input])[0].reshape(1, -1)
   
    # get cosine similarity between input embedding and all the document embeddings
    cos_sim = map(lambda x: cosine_similarity(input_embedding, x)[0][0], doc_vec)
    scores = list(cos_sim)
    # Filter top N recommendations
    recommendations = get_recommendations(N, scores)
    return recommendations

  

In [25]:
input_ingredient = "chicken, onion, spinach, garlic, pasta"
rec_cosine = get_recs_cosine(input_ingredient, N=10)
display(rec_cosine)

recipe  \
0        Extremely Soft White Bread  (Bread Machine)   
1                        Bahama Mama Banana Rum Cake   
2  A1b Bacon Burger Bites on White Polenta Cakes #A1   
3  Copy-Cat Panera Cream of Chicken and Wild Rice...   
4                               Texas Chewy Pralines   
5                                     Elderberry Pie   
6                          Easy Cream of Potato Soup   
7    Old Fashioned Molasses &quot;caramel&quot; Corn   
8                             Donair Meat Sandwiches   
9                                   Oven Baked Tacos   

                                         ingredients score    rating  
0  [hot water, salt, sugar, vegetable oil, white ...   0.0       5.0  
1  [all purpose flour, baking powder, baking soda...   0.0  4.867263  
2  [a    original sauce, bacon, brown sugar, caye...   0.0  4.853836  
3  [all purpose flour, butter, carrot, celery, ch...   0.0  4.823795  
4  [brown sugar, butter, heavy cream, light corn ...   0.0  4.761721  
5  [butter, cinnamon, elderberry, flour, lemon ju...   0.0  4.749467  
6  [butter, chicken broth, dried dill weed, flour...   0.0   4.73081  
7  [baking soda, brown sugar, butter, molasses, p...   0.0  4.730153  
8  [breadcrumb, canned milk, garlic powder, garli...   0.0  4.716243  
9  [diced onion, diced tomato, flour tortillas, g...   0.0   4.70342

# Testing hybrid recommender system

In [26]:
#List of unique user id
df_review['User'].value_counts()

424680        4536
37449         3439
383346        2654
128473        2418
169430        2409
89831         2207
58104         2130
133174        2053
199848        1966
4470          1856
305531        1829
226863        1738
369715        1686
95743         1642
176615        1618
498271        1511
39835         1498
286566        1422
80353         1400
1072593       1397
107583        1375
88099         1371
131126        1363
140132        1349
166642        1318
126440        1315
222564        1314
107135        1296
157425        1228
280271        1226
5060          1187
486725        1137
104295        1132
593927        1131
461834        1086
482376        1073
174096        1071
679953        1031
6357          1026
197023        1021
101823         994
428885         986
163112         986
8688           984
53932          976
136997         973
542159         960
47892          958
204024         949
17803          947
67656          938
29196          938
173579      

In [27]:
df_refined = get_recommendations_1(37449,20)
#Change String to List
df_refined['ingredients'] = df_refined['ingredients'].apply(lambda s: list(ast.literal_eval(s)))
#Sort data corpus
ingredients_corpus = get_and_sort_corpus(df_refined)


In [28]:
input_ingredient = "shrimp, brocolli, rice"
rec_cosine = get_recs_cosine(input_ingredient, N=10)
display(rec_cosine)

recipe  \
0                       Milk-Free, Egg-Free Pancakes   
1  Cheesy Chicken, Bacon &amp; Tater Tot Crock Po...   
2  Amazing Gluten-Free Buttermilk Donuts / Doughnuts   
3                          Black Bean Chocolate Cake   
4                             Shelly's Baked Ricotta   
5                             Basic Vanilla Frosting   
6  Fluffy Eggless Sugar Cookies (Breathtaking Del...   
7  Pumpkin Cheesecake With Gluten Free Gingersnap...   
8     Spinach and Cheese Stuffed Chicken Breast #RSC   
9                Corned Beef and Cabbage (Crock Pot)   

                                         ingredients                 score  \
0  [baking powder, egg, margarine, salt, water, w...   0.12389764189720154   
1  [bacon bits, boneless skinless chicken breasts...   0.08303304016590118   
2  [baking powder, baking soda, butter, buttermil...   0.06536824256181717   
3  [baking powder, baking soda, black beans, coco...   0.05865773931145668   
4  [egg, italian seasoning, marinara sauce, mozza...   0.04275689274072647   
5            [butter, milk, powdered sugar, vanilla]   0.03789009526371956   
6  [all purpose flour, baking powder, butter, mil...  0.037425313144922256   
7  [cream cheese, egg, gingersnap crumbs, ground ...  0.026746714487671852   
8  [black olives, boneless skinless chicken breas...  0.025481000542640686   
9  [apple cider vinegar, cabbage, carrot, corned ...  0.009679105132818222   

     rating  
0  4.743179  
1  4.522532  
2  4.601734  
3  4.608158  
4  4.501546  
5  4.543732  
6  4.504581  
7  4.499891  
8  4.612216  
9  4.486461

In [29]:
input_ingredient = "beef, potato, rice, pepper"
rec_cosine = get_recs_cosine(input_ingredient, N=10)
display(rec_cosine)

recipe  \
0  Cheesecake Factory Key Lime Cheesecake--My Ver...   
1                           Nigella Lawson  Brownies   
2                       Milk-Free, Egg-Free Pancakes   
3                           Caramel Pecan Pound Cake   
4     Spinach and Cheese Stuffed Chicken Breast #RSC   
5                          Black Bean Chocolate Cake   
6  Amazing Gluten-Free Buttermilk Donuts / Doughnuts   
7                 Butter-Less Chocolate Chip Cookies   
8     Incredible Boneless Pork Roast With Vegetables   
9                                     Malva  Pudding   

                                         ingredients score    rating  
0  [butter, cream cheese, egg, flour, graham crac...   0.0       5.0  
1  [caster sugar, dark chocolate, egg, plain flou...   0.0  4.821746  
2  [baking powder, egg, margarine, salt, water, w...   0.0  4.743179  
3  [all purpose flour, baking powder, brown sugar...   0.0  4.688012  
4  [black olives, boneless skinless chicken breas...   0.0  4.612216  
5  [baking powder, baking soda, black beans, coco...   0.0  4.608158  
6  [baking powder, baking soda, butter, buttermil...   0.0  4.601734  
7  [almond extract, baking powder, baking soda, b...   0.0  4.593264  
8  [baby carrots, beef broth, black pepper, bonel...   0.0  4.572661  
9  [apricot jam, baking powder, bicarbonate of so...   0.0  4.545641

In [31]:
input_ingredient = "fish, carrot, rice, celery"
rec_cosine = get_recs_cosine(input_ingredient, N=10)
display(rec_cosine)

recipe  \
0  Cheesecake Factory Key Lime Cheesecake--My Ver...   
1                           Nigella Lawson  Brownies   
2                       Milk-Free, Egg-Free Pancakes   
3                           Caramel Pecan Pound Cake   
4     Spinach and Cheese Stuffed Chicken Breast #RSC   
5                          Black Bean Chocolate Cake   
6  Amazing Gluten-Free Buttermilk Donuts / Doughnuts   
7                 Butter-Less Chocolate Chip Cookies   
8     Incredible Boneless Pork Roast With Vegetables   
9                                     Malva  Pudding   

                                         ingredients score    rating  
0  [butter, cream cheese, egg, flour, graham crac...   0.0       5.0  
1  [caster sugar, dark chocolate, egg, plain flou...   0.0  4.821746  
2  [baking powder, egg, margarine, salt, water, w...   0.0  4.743179  
3  [all purpose flour, baking powder, brown sugar...   0.0  4.688012  
4  [black olives, boneless skinless chicken breas...   0.0  4.612216  
5  [baking powder, baking soda, black beans, coco...   0.0  4.608158  
6  [baking powder, baking soda, butter, buttermil...   0.0  4.601734  
7  [almond extract, baking powder, baking soda, b...   0.0  4.593264  
8  [baby carrots, beef broth, black pepper, bonel...   0.0  4.572661  
9  [apricot jam, baking powder, bicarbonate of so...   0.0  4.545641

# Conclusion
All scores that are attained through the hybrid model are very low. This is largely due to the fact that we are refining the dataset that the content-based recommender is running to under 100 rows. As such, from this list these recipes may not match well with the input ingredients. We need to determine if we what is the best threshold number of recipes for the collaborative filtering method to help improve prediction when running the content-based recommender.

When we run input ingredients with beef and fish, we receive a score of 0.

The recipes being recommended for the fish and beef follow what our EDA process tells us that most recipes are dessert recipes. It seems like when there is no match, the most recommended recipe would be a dessert recipe. This is a huge flaw. 

In future state, we will need to find non-dessert recipes.
